In [1]:
import pandas as pd
import sqlite3
import requests
import numpy as np
import folium
import folium.plugins 

# Data for the RV grouping project

Online I found a complete list of camp grounds in CSV format from http://www.poi-factory.com/node/17657

I will now extract all the required information
- Latitude and Longitude Data
- Name of the Camp Site
- Save the data to a sql3 database for wasy retreival and querying

In [ ]:

df_raw = pd.read_csv('ParksandCampsites.csv', header=None)

In [ ]:
df_raw = df_raw.set_axis(['Longitude', 'Latitude', 'Campsite_Name','Address'], axis=1)
df_raw

In [ ]:
con = sqlite3.connect('Campsite_data.db')
df_raw.to_sql('Sites',con)
con.close()

In [2]:
con = sqlite3.connect('Campsite_data.db')
query = ''' SELECT Campsite_Name, Latitude, Longitude FROM Sites WHERE Campsite_Name like '%RV%' AND Campsite_Name not like '%closed%'   '''
df_RV = pd.read_sql_query(query,con).set_index('Campsite_Name').drop_duplicates()
con.close
df_RV


Latitude   Longitude
Campsite_Name                                                      
10 Acres Campground and RV Park               44.030277  -73.403468
1015 RV Park                                  26.145834  -97.958195
11 Bridges Campground and RV Park             51.415188 -112.632344
115 Creek Rest Area (no services)             58.716979 -124.912576
1202 Motor Inn and RV Park                    62.387044 -140.873463
...                                                 ...         ...
Zion RV and Campground                        37.236637 -112.856060
Zion West RV Park                             37.231969 -113.364556
Zion's Gate RV Resort                         37.170192 -113.373832
Zuni Village RV Park                          35.224768 -114.014515
Zunino/Jiggs Reservoir Recreation Area - BLM  40.457238 -115.653227

[5311 rows x 2 columns]

## Map with the location Data

In [3]:
# create map of RV parks using latitude and longitude values
latitude = df_RV['Latitude'].mean()
longitude = df_RV['Longitude'].mean()
map_national_RV_parks = folium.Map(location=[latitude, longitude], zoom_start=4)

# add markers to map
marker_cluster = folium.plugins.MarkerCluster().add_to(map_national_RV_parks)
for lat, lng, name in zip(df_RV['Latitude'], df_RV['Longitude'], df_RV.reset_index()['Campsite_Name']):
    label = "<a  target='_blank' href='https://www.google.com/search?q={}'>{}</a>".format(name.replace(' ','%20'),name)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(marker_cluster)  

map_national_RV_parks

In [4]:
map_national_RV_parks.save('RV_Parks_Map.html')

In [ ]:
CLIENT_ID = 'XXX' # your Foursquare ID
CLIENT_SECRET = 'XXX' # your Foursquare Secret
ACCESS_TOKEN = 'XXX' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 60
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

## Neighboring venues data

Now I will use Foursquare to download neighboring venue data and save them to my sql3 database

In [ ]:
try:
    con = sqlite3.connect('Campsite_data.db')
    query = ''' SELECT distinct(Campsite_Name) FROM Venues'''
    completed_venues = pd.read_sql_query(query,con)['Campsite_Name'].tolist()
    con.close
except:
    completed_venues = []
    
print('Number of completed venues that will not be run again: {}'.format(len(completed_venues)))
for key, item in df_RV.reset_index().iterrows():
    venues_list = []
    
    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        item['Latitude'], 
        item['Longitude'], 
        10000, #radius
        LIMIT)
    
    if not (item['Campsite_Name'] in completed_venues):
        print('New Site: {}'.format(item['Campsite_Name']))
        results = requests.get(url).json()["response"]['groups'][0]['items']
        for v in results:
            temp = {}
            temp['Campsite_Name']= item['Campsite_Name']
            temp['Latitude']= item['Latitude']
            temp['Longitude']= item['Longitude']
            temp['Venue']=v['venue']['name']
            temp['Venue_Latitude']=v['venue']['location']['lat']
            temp['Venue_Longitude']=v['venue']['location']['lng']  
            temp['Venue_Category']=v['venue']['categories'][0]['name']
            venues_list.append(temp)
        
        nearby_venues = pd.DataFrame(venues_list)
        con = sqlite3.connect('Campsite_data.db')
        nearby_venues.to_sql('Venues',con,if_exists='append')
        con.close()

## Check data integrity

In [7]:
con = sqlite3.connect('Campsite_data.db')
query = ''' SELECT * FROM Venues'''
completed_venues = pd.read_sql_query(query,con)
completed_venues

index                                 Campsite_Name   Latitude  \
0           0               10 Acres Campground and RV Park  44.030277   
1           1               10 Acres Campground and RV Park  44.030277   
2           2               10 Acres Campground and RV Park  44.030277   
3           3               10 Acres Campground and RV Park  44.030277   
4           4               10 Acres Campground and RV Park  44.030277   
...       ...                                           ...        ...   
180228     49                          Zuni Village RV Park  35.224768   
180229     50                          Zuni Village RV Park  35.224768   
180230     51                          Zuni Village RV Park  35.224768   
180231     52                          Zuni Village RV Park  35.224768   
180232      0  Zunino/Jiggs Reservoir Recreation Area - BLM  40.457238   

         Longitude                            Venue  Venue_Latitude  \
0       -73.403468                Goodies Snack Bar       44.063204   
1       -73.403468            The Bridge Restaurant       44.036137   
2       -73.403468       West Addison General Store       44.064368   
3       -73.403468                  Stewart's Shops       44.047061   
4       -73.403468  Crown Point State Historic Site       44.028508   
...            ...                              ...             ...   
180228 -114.014515                 Rattlesnake wash       35.205185   
180229 -114.014515                            Hertz       35.257405   
180230 -114.014515    American Woodmark Corporation       35.266018   
180231 -114.014515             Kingman Airport Cafe       35.258943   
180232 -115.653227                        Jiggs Bar       40.427223   

        Venue_Longitude       Venue_Category  
0            -73.407221          Snack Place  
1            -73.417700  American Restaurant  
2            -73.406900    Convenience Store  
3            -73.459426    Convenience Store  
4            -73.426759        Historic Site  
...                 ...                  ...  
180228      -113.944803                River  
180229      -113.947516  Rental Car Location  
180230      -113.950768              Factory  
180231      -113.944210                 Café  
180232      -115.665382                  Bar  

[180233 rows x 8 columns]